# Première analyse rapide des données

In [1]:
# import des packages importants
import numpy as np 
import matplotlib.pyplot as plt 
import pandas as pd 
import seaborn as sns

In [2]:
data_url = "https://gitlab.inria.fr/learninglab/mooc-rr/mooc-rr-ressources/-/raw/master/module3/Practical_session/Subject6_smoking.csv?inline=false" 

In [3]:
raw_data = pd.read_csv(data_url)
raw_data[:10]

Smoker Status   Age
0    Yes  Alive  21.0
1    Yes  Alive  19.3
2     No   Dead  57.5
3     No  Alive  47.1
4    Yes  Alive  81.4
5     No  Alive  36.8
6     No  Alive  23.8
7    Yes   Dead  57.5
8    Yes  Alive  24.8
9    Yes  Alive  49.5

In [4]:
raw_data[raw_data.isnull().any(axis=1)] 

Empty DataFrame
Columns: [Smoker, Status, Age]
Index: []

Donc ici pas de point manquant -> pas besoin de modifier les données.

On compte les morts.

In [5]:
dead = raw_data['Status'].value_counts()['Dead']
alive = raw_data['Status'].value_counts()['Alive']
print(f'number alive = {alive}')
print(f'number dead = {dead}')
print(f'total number = {alive + dead}')
smoker = raw_data['Smoker'].value_counts()['Yes']
non_smoker = raw_data['Smoker'].value_counts()['No']
print(f'number smoker = {smoker}')
print(f'number non smoker = {non_smoker}')


number alive = 945
number dead = 369
total number = 1314
number smoker = 582
number non smoker = 732


# Question 1

In [6]:
tab = pd.crosstab(raw_data.Status, raw_data.Smoker) # on a bien le bon nombre de vivants et de morts
tab

Smoker   No  Yes
Status          
Alive   502  443
Dead    230  139

In [7]:
numpy_data = np.array(tab)
print(numpy_data)
ratio_smoker = numpy_data[1,1]/smoker
ratio_non_smoker = numpy_data[1,0]/non_smoker
print(f'ratio_smoker = {ratio_smoker:.6f}')
print(f'ratio_non_smoker = {ratio_non_smoker:.6f}')

[[502 443]
 [230 139]]
ratio_smoker = 0.238832
ratio_non_smoker = 0.314208


Ah bah c'est dommage, les gens qui ne fument pas meurent plus que les gens qui fument... embêtant.

# Question 2 

In [8]:
raw_data.loc[((raw_data.Age < 34) & (raw_data.Age >= 18) ),  'AgeGroup'] = '1'
raw_data.loc[((raw_data.Age < 55) & (raw_data.Age >= 34) ),  'AgeGroup'] = '2'
raw_data.loc[((raw_data.Age < 65) & (raw_data.Age >= 55) ),  'AgeGroup'] = '3'
raw_data.loc[(raw_data.Age >= 65),  'AgeGroup'] = '4'

raw_data[:10]

Smoker Status   Age AgeGroup
0    Yes  Alive  21.0        1
1    Yes  Alive  19.3        1
2     No   Dead  57.5        3
3     No  Alive  47.1        2
4    Yes  Alive  81.4        4
5     No  Alive  36.8        2
6     No  Alive  23.8        1
7    Yes   Dead  57.5        3
8    Yes  Alive  24.8        1
9    Yes  Alive  49.5        2

In [9]:
for age_group in ['1', '2', '3', '4']:
    print('##################')
    print(f'Groupe d\'age : {age_group}')
    tab_class = raw_data.loc[(raw_data.AgeGroup == age_group)]
    dead = tab_class['Status'].value_counts()['Dead']
    alive = tab_class['Status'].value_counts()['Alive']
    print(f'number alive = {alive}')
    print(f'number dead = {dead}')
    print(f'total number = {alive + dead}')
    smoker = tab_class['Smoker'].value_counts()['Yes']
    non_smoker = tab_class['Smoker'].value_counts()['No']
    print(f'number smoker = {smoker}')
    print(f'number non smoker = {non_smoker}')
    tab_class = pd.crosstab(tab_class.Status, tab_class.Smoker) # on a bien le bon nombre de vivants et de morts
    display(tab_class)
    numpy_data = np.array(tab_class)
  
    ratio_smoker = numpy_data[1,1]/smoker
    ratio_non_smoker = numpy_data[1,0]/non_smoker
    print(f'ratio_smoker = {ratio_smoker:.6f}')
    print(f'ratio_non_smoker = {ratio_non_smoker:.6f}')
    print('##################\n')


##################
Groupe d'age : 1
number alive = 387
number dead = 11
total number = 398
number smoker = 179
number non smoker = 219


Smoker   No  Yes
Status          
Alive   213  174
Dead      6    5

ratio_smoker = 0.027933
ratio_non_smoker = 0.027397
##################

##################
Groupe d'age : 2
number alive = 378
number dead = 60
total number = 438
number smoker = 239
number non smoker = 199


Smoker   No  Yes
Status          
Alive   180  198
Dead     19   41

ratio_smoker = 0.171548
ratio_non_smoker = 0.095477
##################

##################
Groupe d'age : 3
number alive = 145
number dead = 91
total number = 236
number smoker = 115
number non smoker = 121


Smoker  No  Yes
Status         
Alive   81   64
Dead    40   51

ratio_smoker = 0.443478
ratio_non_smoker = 0.330579
##################

##################
Groupe d'age : 4
number alive = 35
number dead = 207
total number = 242
number smoker = 49
number non smoker = 193


Smoker   No  Yes
Status          
Alive    28    7
Dead    165   42

ratio_smoker = 0.857143
ratio_non_smoker = 0.854922
##################



**Analyse :** 
- Dans le groupe 1 : chez les plus jeunes (18-34 ans), le fait de fumer n'influe pas énormément sur le taux de mortalité. 
- Dans le groupe 2 : fumer tue, le taux de mortalité est presque 2 fois plus élévé chez les fumeurs. 
- Dans le groupe 3 : tout le monde meurt. Mais un peu plus souvent chez les fumeurs. 
- Dans le groupe 4 : c'est catastrophique (mais normal, ils sont vieux), tout le monde meurt. 

C'est donc le nombre de membres de la catégorie 4 qui biaise les données globales : il y en a beaucoup, dont une grande partie de non-fumeurs, là où pour les autres catégories, la proportion de fumeurs et de non-fumeurs est presque équivalente. Puisque beaucoup de vieux meurent, la consommation de tabac ne semble pas faire varier le taux, ce qui biaise le ratio global.